# This lab contains exercises for the Bioinformatics with Python Lab held on November 19th, 2024 during the CSHL Advanced Sequencing Technologies & Bioinformatics Analysis course

## VCFs and Pandas

#### We will conclude by doing some exercises that combine analysis of variant call files (VCFs) and the pandas library. First, let's import pandas and pysam:

In [8]:
import pandas as pd
import pysam

#### 1. Write code to read in the VCF using pysam. How would you print the header?:

In [9]:
vcf_file = pysam.VariantFile("../../data/Exome_Norm_HC_calls.filtered.PASS.vcf", index_filename=None)
print(vcf_file.header)

##fileformat=VCFv4.2
##FILTER=<ID=PASS,Description="All filters passed">
##FILTER=<ID=FS_gt_200,Description="FS > 200.0">
##FILTER=<ID=FS_gt_60,Description="FS > 60.0">
##FILTER=<ID=LowQual,Description="Low quality">
##FILTER=<ID=QD_lt_2,Description="QD < 2.0">
##FILTER=<ID=RPRS_lt_n8,Description="MQ < 40.0">
##FILTER=<ID=SOR_gt_10,Description="SOR > 10.0">
##FILTER=<ID=SOR_gt_3,Description="SOR > 3.0">
##FORMAT=<ID=AD,Number=R,Type=Integer,Description="Allelic depths for the ref and alt alleles in the order listed">
##FORMAT=<ID=DP,Number=1,Type=Integer,Description="Approximate read depth (reads with MQ=255 or with bad mates are filtered)">
##FORMAT=<ID=GQ,Number=1,Type=Integer,Description="Genotype Quality">
##FORMAT=<ID=GT,Number=1,Type=String,Description="Genotype">
##FORMAT=<ID=PL,Number=G,Type=Integer,Description="Normalized, Phred-scaled likelihoods for genotypes as defined in the VCF specification">
##GATKCommandLine=<ID=HaplotypeCaller,CommandLine="HaplotypeCaller --bam-output

#### 2. Scroll through and look at the rows with the ##FORMAT flags. What do these rows mean and why are they important?

These rows contain information that can be used to interpret what the data in the VCF means

#### 3. Write code below to view the first 30 variants in the vcf. What kind of variants do you see in this list? How can you tell?

In [10]:
print("#CHROM POS ID REF ALT QUAL FILTER INFO FORMAT HCC1395BL_DNA")
for index, record in enumerate(vcf_file):
   if index == 30:
       break
   else:
       print(record)

#CHROM POS ID REF ALT QUAL FILTER INFO FORMAT HCC1395BL_DNA
chr17	60996	.	G	C	106.64	PASS	AC=1;AF=0.5;AN=2;BaseQRankSum=0;DP=7;ExcessHet=3.0103;FS=0;MLEAC=1;MLEAF=0.5;MQ=45.17;MQRankSum=-1.204;QD=15.23;ReadPosRankSum=-0.652;SOR=0.495	GT:AD:DP:GQ:PL	0/1:4,3:7:99:114,0,159

chr17	61004	.	C	T	103.64	PASS	AC=1;AF=0.5;AN=2;BaseQRankSum=0;DP=8;ExcessHet=3.0103;FS=0;MLEAC=1;MLEAF=0.5;MQ=43.32;MQRankSum=-0.647;QD=12.95;ReadPosRankSum=-0.703;SOR=0.368	GT:AD:DP:GQ:PL	0/1:5,3:8:99:111,0,188

chr17	61907	.	A	G	53.32	PASS	AC=2;AF=1;AN=2;DP=4;ExcessHet=3.0103;FS=0;MLEAC=1;MLEAF=0.5;MQ=49.93;QD=26.66;SOR=2.303	GT:AD:DP:GQ:PL	1/1:0,2:2:6:65,6,0

chr17	62742	.	C	G	364.64	PASS	AC=1;AF=0.5;AN=2;BaseQRankSum=3.846;DP=45;ExcessHet=3.0103;FS=2.869;MLEAC=1;MLEAF=0.5;MQ=59.96;MQRankSum=0;QD=24.31;ReadPosRankSum=2.598;SOR=1.942	GT:AD:DP:GQ:PL	0/1:3,12:15:29:372,0,29

chr17	63304	.	A	G	159.96	PASS	AC=2;AF=1;AN=2;DP=6;ExcessHet=3.0103;FS=0;MLEAC=2;MLEAF=1;MQ=60;QD=31.99;SOR=1.981	GT:AD:DP:GQ:PL	1/1:0,5:5:15:174,

This subset contains substitutions and deletions. This can be determined by comparing the sequences for `ref` and `alt`. For substitutions, they have equal length, while for deletions, the length of `ref` is greater than the length of `alt`.

#### Run the code below to convert the VCF to a pandas dataframe:

In [11]:
columns = ["chrom", "pos", "id", "ref", "alt", "qual", "filter",
          "dp", "gt", "ad", "gq"]
vcf_data = []
for record in vcf_file:
   sample_data = record.samples["HCC1395BL_DNA"]
   vcf_data.append({"chrom": record.chrom,
                  "pos": record.pos,
                  "id": record.id,
                  "ref": record.ref,
                  "alt": ','.join(record.alts),
                  "qual": record.qual,
                  "filter": ';'.join(record.filter.keys()),
                  "dp": sample_data.get("DP"),
                  "gt": sample_data.get("GT"),
                  "ad": sample_data.get("AD"),
                  "gq":sample_data.get("GQ")})
vcf_data = pd.DataFrame(vcf_data)
vcf_data["chrom"] = vcf_data["chrom"].str.replace('chr', '', regex=False).astype(int)

#### 4. How many rows are in the dataframe? What pandas command can you use to determine this? 

In [12]:
len(vcf_data)

11338

#### 5. We would like to take a random sample of 20 entries from the dataframe. How would we do this in pandas? Name the new dataset `vcf_subset`. Set the random state to equal 7 for reproducibility.

In [13]:
vcf_subset = vcf_data.sample(n=20, random_state=7)

#### 6. Suppose we want to sort the sample so that the variant positions are in **descending order**. How would you do this using pandas?

In [14]:
vcf_subset.sort_values(by="pos", ascending=False)

chrom       pos    id                             ref alt         qual  \
11226     17  82664414  None                               A   G   686.640015   
10883     17  81282112  None                               C   T  1187.640015   
10048     17  76974871  None                               C   T    58.320000   
9229      17  74249847  None  CCACTGTGGGGCTCCTGGGAGACGGAGCCT   C  1340.030029   
9099      17  73235465  None                               A   C  3700.060059   
8614      17  68129367  None                               T   A  2030.640015   
8396      17  66036113  None                               A   T    37.320000   
8144      17  63810333  None                               C   T   260.640015   
8078      17  63530079  None                               T   G  1360.640015   
7412      17  56391225  None                               A   G    35.480000   
6674      17  48121514  None                               G   C  5765.060059   
6176      17  43875844  None                               G   A    56.320000   
4569      17  30142764  None                               T   G    58.320000   
3830      17  22131400  None                               A   T   121.839996   
3816      17  22123931  None                               A   C    78.320000   
3648      17  21704572  None                               G   A  1399.640015   
2688      17  16844080  None                               C   G   512.640015   
2403      17  13635911  None                               T   C    70.839996   
1559      17   7738550  None                               C   T    53.639999   
991       17   5350822  None                               C   G    98.639999   

      filter   dp      gt        ad  gq  
11226   PASS   55  (0, 1)  (30, 25)  99  
10883   PASS   78  (0, 1)  (34, 44)  99  
10048   PASS    2  (1, 1)    (0, 2)   6  
9229    PASS   30  (1, 1)   (0, 30)  92  
9099    PASS  111  (1, 1)  (0, 111)  99  
8614    PASS  150  (0, 1)  (74, 76)  99  
8396    PASS    2  (1, 1)    (0, 2)   6  
8144    PASS   15  (0, 1)    (6, 9)  99  
8078    PASS  103  (0, 1)  (53, 50)  99  
7412    PASS    1  (1, 1)    (0, 1)   3  
6674    PASS  178  (1, 1)  (0, 178)  99  
6176    PASS    2  (1, 1)    (0, 2)   6  
4569    PASS    2  (1, 1)    (0, 2)   6  
3830    PASS    3  (1, 1)    (0, 3)   9  
3816    PASS    2  (1, 1)    (0, 2)   6  
3648    PASS  117  (0, 1)  (77, 40)  99  
2688    PASS   65  (0, 1)  (44, 21)  99  
2403    PASS    3  (1, 1)    (0, 3)   9  
1559    PASS    3  (0, 1)    (1, 2)  26  
991     PASS   11  (0, 1)    (7, 4)  99

#### 7. We would like to only include variants that have a read depth >= 50.0 and a genotype quality >= 70.0. How would you do this using pandas?

In [15]:
vcf_subset[(vcf_subset["dp"] >= 50.0) & (vcf_subset["gq"] >= 70.0)]

chrom       pos    id ref alt         qual filter   dp      gt  \
6674      17  48121514  None   G   C  5765.060059   PASS  178  (1, 1)   
8614      17  68129367  None   T   A  2030.640015   PASS  150  (0, 1)   
11226     17  82664414  None   A   G   686.640015   PASS   55  (0, 1)   
2688      17  16844080  None   C   G   512.640015   PASS   65  (0, 1)   
3648      17  21704572  None   G   A  1399.640015   PASS  117  (0, 1)   
8078      17  63530079  None   T   G  1360.640015   PASS  103  (0, 1)   
9099      17  73235465  None   A   C  3700.060059   PASS  111  (1, 1)   
10883     17  81282112  None   C   T  1187.640015   PASS   78  (0, 1)   

             ad  gq  
6674   (0, 178)  99  
8614   (74, 76)  99  
11226  (30, 25)  99  
2688   (44, 21)  99  
3648   (77, 40)  99  
8078   (53, 50)  99  
9099   (0, 111)  99  
10883  (34, 44)  99

## Final Exercise

#### A clinical colleague has asked you to examine the VCF to see if there are any frameshift variants in the coding regions of the *P2RX5* gene. How many frameshift variants are there? Write your code below to answer this question. The exon coordinates for the *P2RX5* gene are provided in the cell below.

In [16]:
exon_list = [[3695868,3696155], [3691643,3691794], [3690955,3691027],
             [3690604,3690680], [3690426,3690523], [3690069,3690150],
             [3689491,3689630], [3688625,3688759], [3688011,3688105],
             [3681895,3681978], [3679589,3679784], [3673226,3673226]]

In [17]:
def in_exon(pos: int, exon_list:list[list]) -> bool:
   """Check if a coordinate occurs in an exon
  
   :param pos: A genomic position
   :param exon_list: A list containing genomic coordinates for exons, with a list 
   representing each exon

   :return ``True`` if the position occurs on an exon, ``False`` if not
   """
   for exon in exon_list:
       if pos >= exon[0] and pos <= exon[1]:
           return True
   return False

vcf_subset = vcf_data[vcf_data["pos"].apply(lambda pos: in_exon(pos, exon_list))]
vcf_subset = vcf_subset[vcf_subset.apply(lambda row: len(row["ref"]) % 3 != len(row["alt"]) % 3, axis=1)]

In [18]:
vcf_subset

chrom      pos    id ref alt        qual filter  dp      gt        ad  gq
578     17  3690982  None  TG   T  669.599976   PASS  45  (0, 1)  (20, 25)  99